In [3]:
cd ..

C:\Users\shubb\Downloads\Project


In [45]:
pwd

'C:\\Users\\shubb\\Downloads\\Project\\yolov5'

In [25]:
cd ..

C:\Users\shubb\Downloads\Project\yolov5


In [43]:
!python train.py --img 640 --epochs 100 --data dataset.yaml --weights yolov5s.pt

WARNING invalid check_version(None, >=1.4.1) requested, please check values.

C:\Users\shubb\Downloads\Project\yolov5\utils\general.py:32: UserWarning: pkg_resources is deprecated as an API. See https://setuptools.pypa.io/en/latest/pkg_resources.html. The pkg_resources package is slated for removal as early as 2025-11-30. Refrain from using this package or pin to Setuptools<81.
  import pkg_resources as pkg
train: weights=yolov5s.pt, cfg=, data=dataset.yaml, hyp=data\hyps\hyp.scratch-low.yaml, epochs=100, batch_size=16, imgsz=640, rect=False, resume=False, nosave=False, noval=False, noautoanchor=False, noplots=False, evolve=None, evolve_population=data\hyps, resume_evolve=None, bucket=, cache=None, image_weights=False, device=, multi_scale=False, single_cls=False, optimizer=SGD, sync_bn=False, workers=8, project=runs\train, name=exp, exist_ok=False, quad=False, cos_lr=False, label_smoothing=0.0, patience=100, freeze=[0], save_period=-1, seed=0, local_rank=-1, entity=None, upload_dataset=False, bbox_interval=-1, artifact_alias=latest, ndjson_console=False, ndjson

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)

  with torch.cuda.amp.autocast(amp):

      59/99      3.84G    0.01428    0.01017   0.002623         48        640:  69%|######9   | 381/551 [00:56<00:25,  6.71it/s]
      59/99      3.84G    0.01428    0.01017   0.002623         48        640:  69%|######9   | 382/551 [00:56<00:24,  6.79it/s]C:\Users\shubb\Downloads\Project\yolov5\train.py:414: FutureWar

In [99]:
!python detect.py --weights ./runs/train/exp7/weights/best.pt --source ../data/test_dataset/ --save-txt --save-conf

WARNING invalid check_version(None, >=1.4.1) requested, please check values.

A module that was compiled using NumPy 1.x cannot be run in
NumPy 2.2.6 as it may crash. To support both 1.x and 2.x
versions of NumPy, modules must be compiled with NumPy 2.0.
Some module may need to rebuild instead e.g. with 'pybind11>=2.12'.

If you are a user of the module, the easiest solution will be to
downgrade to 'numpy<2' or try to upgrade the affected module.
We expect that some modules will need time to support NumPy 2.

Traceback (most recent call last):  File "C:\Users\shubb\Downloads\Project\yolov5\detect.py", line 48, in <module>
    from models.common import DetectMultiBackend
  File "C:\Users\shubb\Downloads\Project\yolov5\models\common.py", line 18, in <module>
    import pandas as pd
  File "C:\Users\shubb\anaconda3\Lib\site-packages\pandas\__init__.py", line 39, in <module>
    from pandas.compat import (
  File "C:\Users\shubb\anaconda3\Lib\site-packages\pandas\compat\__init__.py", line 27, in <module>
    from pandas.compat.pyarrow import (
  File "C:\Users\shubb

In [ ]:
import os
import cv2
import numpy as np
import pandas as pd

# === CLASS MAPPING ===
class_id_map = {
    0: 'circle',
    1: 'square',
    2: 'triangle'
}

# === COLOR DETECTOR ===
def classify_color(roi_rgb):
    avg_color = np.mean(roi_rgb.reshape(-1, 3), axis=0)
    r, g, b = avg_color
    if r > g and r > b:
        return "red"
    elif g > r and g > b:
        return "green"
    elif b > r and b > g:
        return "blue"
    else:
        return "unknown"

# === BOUNDING BOX CONVERTER ===
def yolo_to_xyxy(x_center, y_center, w, h, img_width, img_height):
    x1 = int((x_center - w / 2) * img_width)
    y1 = int((y_center - h / 2) * img_height)
    x2 = int((x_center + w / 2) * img_width)
    y2 = int((y_center + h / 2) * img_height)
    return max(0, x1), max(0, y1), min(x2, img_width-1), min(y2, img_height-1)

# === ROBUST MATCHER (label → image) ===
def match_image_file(label_file, image_dir):
    base_key = label_file.split("_png")[0]
    for img_file in os.listdir(image_dir):
        if base_key in img_file:
            return os.path.join(image_dir, img_file), img_file  # full path, filename
    return None, None

# === MAIN FUNCTION ===
def convert_yolo_output_to_submission(label_dir, image_dir, output_csv='submission.csv'):
    output_rows = []

    for label_file in sorted(os.listdir(label_dir)):
        if not label_file.endswith(".txt"):
            continue

        image_path, image_name = match_image_file(label_file, image_dir)
        if image_path is None:
            print(f"⚠️ Could not match label file to image: {label_file}")
            continue

        image = cv2.imread(image_path)
        if image is None:
            print(f"⚠️ Could not read image: {image_path}")
            continue

        image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        img_h, img_w = image.shape[:2]

        shape_color_preds = set()

        with open(os.path.join(label_dir, label_file), 'r') as f:
            lines = f.readlines()
            if not lines:
                print(f"⚠️ No predictions in: {label_file}")
            for line in lines:
                parts = line.strip().split()
                if len(parts) < 5:
                    continue
                class_id = int(parts[0])
                x_center, y_center, w, h = map(float, parts[1:5])
                x1, y1, x2, y2 = yolo_to_xyxy(x_center, y_center, w, h, img_w, img_h)

                roi = image_rgb[y1:y2, x1:x2]
                shape = class_id_map.get(class_id, "unknown")
                color = classify_color(roi)

                if shape != "unknown" and color != "unknown":
                    shape_color_preds.add((shape, color))
        output_rows.append({
            "image_path": f"test_dataset/{image_name}",
            "label": str(list(shape_color_preds))  # Will be "[]" if empty
        })

  
    pd.DataFrame(output_rows).to_csv(output_csv, index=False)
    print(f"submission.csv saved at: {output_csv}")


: 

In [89]:
convert_yolo_output_to_submission(
    label_dir='runs/detect/exp3/labels',   # or expN depending on your folder
    image_dir='data/images/test',
    output_csv='submission.csv'
)


✅ submission.csv saved at: submission.csv


In [101]:
import os
import cv2
import numpy as np
import pandas as pd

# === CLASS MAPPING ===
class_id_map = {
    0: 'circle',
    1: 'square',
    2: 'triangle'
}

# === COLOR DETECTOR ===
def classify_color(roi_rgb):
    avg_color = np.mean(roi_rgb.reshape(-1, 3), axis=0)
    r, g, b = avg_color
    if r > g and r > b:
        return "red"
    elif g > r and g > b:
        return "green"
    elif b > r and b > g:
        return "blue"
    else:
        return "unknown"

# === BOUNDING BOX CONVERTER ===
def yolo_to_xyxy(x_center, y_center, w, h, img_width, img_height):
    x1 = int((x_center - w / 2) * img_width)
    y1 = int((y_center - h / 2) * img_height)
    x2 = int((x_center + w / 2) * img_width)
    y2 = int((y_center + h / 2) * img_height)
    return max(0, x1), max(0, y1), min(x2, img_width-1), min(y2, img_height-1)

# === ROBUST MATCHER ===
def match_label_file(image_filename, label_dir):
    basename = os.path.splitext(os.path.basename(image_filename))[0]
    for label_file in os.listdir(label_dir):
        if basename in label_file and label_file.endswith(".txt"):
            return os.path.join(label_dir, label_file)
    return None

# === MAIN PIPELINE ===
def generate_submission_from_test_csv(test_csv_path, label_dir, image_dir, output_csv='submission.csv'):
    test_df = pd.read_csv(test_csv_path)
    results = []

    for _, row in test_df.iterrows():
        img_rel_path = row['image_path']
        img_path = os.path.join(image_dir, os.path.basename(img_rel_path))

        label_file = match_label_file(img_rel_path, label_dir)
        if not os.path.exists(img_path) or not label_file:
            results.append({'image_path': img_rel_path, 'label': "[]"})
            continue

        image = cv2.imread(img_path)
        if image is None:
            results.append({'image_path': img_rel_path, 'label': "[]"})
            continue

        image_rgb = cv2.cvtColor(image, cv2.COLOR_BGR2RGB)
        img_h, img_w = image.shape[:2]

        shape_color_preds = set()
        with open(label_file, 'r') as f:
            for line in f:
                parts = line.strip().split()
                if len(parts) < 5:
                    continue
                class_id = int(parts[0])
                x_center, y_center, w, h = map(float, parts[1:5])
                x1, y1, x2, y2 = yolo_to_xyxy(x_center, y_center, w, h, img_w, img_h)

                roi = image_rgb[y1:y2, x1:x2]
                shape = class_id_map.get(class_id, "unknown")
                color = classify_color(roi)

                if shape != "unknown" and color != "unknown":
                    shape_color_preds.add((shape, color))

        results.append({
            'image_path': img_rel_path,
            'label': str(list(shape_color_preds))
        })

    submission_df = pd.DataFrame(results)
    submission_df.to_csv(output_csv, index=False)
    return submission_df.head()

generate_submission_from_test_csv(
    test_csv_path="C:/Users/shubb/Downloads/Project/data/test.csv",
    label_dir="C:/Users/shubb/Downloads/Project/yolov5/runs/detect/exp5/labels",
    image_dir="C:/Users/shubb/Downloads/Project/data/test_dataset",
    output_csv='submission.csv'
)


image_path                                              label
0  test_dataset/img_0.png                                [('circle', 'red')]
1  test_dataset/img_1.png             [('circle', 'red'), ('square', 'red')]
2  test_dataset/img_2.png           [('circle', 'red'), ('circle', 'green')]
3  test_dataset/img_3.png  [('triangle', 'blue'), ('triangle', 'red'), ('...
4  test_dataset/img_4.png                              [('square', 'green')]